# Clustering 
___
## DBSCAN(Density-Based Spatial Clustering of Applications with Noise)
  - Reference: 학교알리미 공개용 데이터 (서울시 중학교 졸업생의 진로현황)

In [ ]:
import pandas as pd
import folium

* 데이터 읽어오기

In [ ]:
from google.colab import files
uploaded= files.upload()
filename= list(uploaded.keys())[0]
filename

Saving 2016_middle_shcool_graduates_report.xlsx to 2016_middle_shcool_graduates_report (1).xlsx


'2016_middle_shcool_graduates_report.xlsx'

In [ ]:
df = pd.read_excel(filename, header=0, engine='openpyxl')
del df['Unnamed: 0']

# 열 이름 배열 출력 
print(df.columns.values)

['지역' '학교명' '코드' '유형' '주야' '남학생수' '여학생수' '일반고' '특성화고' '과학고' '외고_국제고'
 '예고_체고' '마이스터고' '자사고' '자공고' '기타진학' '취업' '미상' '위도' '경도']


* 데이터 프레임 정보 확인 

In [ ]:
# 데이터 확인 
print(df.head())
print('\n')

# 데이터 자료형 
print(df.info())
print('\n')

# 데이터 통계
print(df.describe())

    지역               학교명  코드  유형  주야  ...   기타진학  취업     미상         위도          경도
0  성북구    서울대학교사범대학부설중학교   3  국립  주간  ...  0.004   0  0.000  37.594942  127.038909
1  종로구  서울대학교사범대학부설여자중학교   3  국립  주간  ...  0.031   0  0.000  37.577473  127.003857
2  강남구             개원중학교   3  공립  주간  ...  0.009   0  0.003  37.491637  127.071744
3  강남구             개포중학교   3  공립  주간  ...  0.019   0  0.000  37.480439  127.062201
4  서초구             경원중학교   3  공립  주간  ...  0.010   0  0.000  37.510750  127.008900

[5 rows x 20 columns]


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 415 entries, 0 to 414
Data columns (total 20 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   지역      415 non-null    object 
 1   학교명     415 non-null    object 
 2   코드      415 non-null    int64  
 3   유형      415 non-null    object 
 4   주야      415 non-null    object 
 5   남학생수    415 non-null    int64  
 6   여학생수    415 non-null    int64  
 7   일반고     415 non-null    float64
 8

* 지도위에 위치 표시
  - 위도와 경도를 CircleMarker 함수에 전달 
  - 각 학교의 위치를 원형 마커로 표기 
  - 학교명은 popup 옵션 

In [26]:
mschool_map = folium.Map(location=[37.55, 126.98], tiles='Stamen Terrain', 
                          zoom_start= 12)

# 중학교 위치 정보를 CircleMarker로 표기 
for name, lat, lng in zip(df.학교명, df.위도, df.경도):
  folium.CircleMarker([lat, lng],
                      radius = 5, 
                      color='brown',
                      file=True, 
                      fill_color ='coral',
                      fill_opacity = 0.7,       # 투명도
                      popup=name
  ).add_to(mschool_map)


title_html = '<h3 align="center" style="font-size:20px"><b>서울시 중학교 위치</b></h3>'   
mschool_map.get_root().html.add_child(folium.Element(title_html))
mschool_map

* 데이터 전처리
  - 텍스트 데이터 더미 변수로 변환 

In [ ]:
# 원핫인코딩 (더미변수)
from sklearn import preprocessing

label_encoder = preprocessing.LabelEncoder()            # label encoder
onehot_encoder = preprocessing.OneHotEncoder()          # one hot encoder 

onehot_location = label_encoder.fit_transform(df['지역'])
onehot_code = label_encoder.fit_transform(df['코드'])
onehot_type = label_encoder.fit_transform(df['유형'])
onehot_day = label_encoder.fit_transform(df['주야'])

df['location'] = onehot_location
df['code'] = onehot_code
df['type'] = onehot_type
df['day'] = onehot_day

df.head(2)

지역               학교명  코드  유형  주야  ...          경도  location  code  type  day
0  성북구    서울대학교사범대학부설중학교   3  국립  주간  ...  127.038909        16     0     1    0
1  종로구  서울대학교사범대학부설여자중학교   3  국립  주간  ...  127.003857        22     0     1    0

[2 rows x 24 columns]

* 데이터 학습 및 모델 생성

In [ ]:
# DBSCAN 군집 모형 가져오기 

from sklearn import cluster 

# feature 
columns_list = [9, 10, 13]
X = df.iloc[:, columns_list]
print(X[:5])
print('\n')


# 설명변수(Feature)에 변수 데이터 정규화
X = preprocessing.StandardScaler().fit(X).transform(X)


# DBSCAN 모형 객체 생성 
dbm = cluster.DBSCAN(eps=0.2, min_samples=5)

# 모형 학습 
dbm.fit(X)

# 예측(군집)
cluster_label = dbm.labels_
print(cluster_label)
print('\n')

# 예측 결과를 데이터 프레임에 추가 
df['Cluster'] = cluster_label
print(df.head())

     과학고  외고_국제고    자사고
0  0.018   0.007  0.227
1  0.000   0.035  0.043
2  0.009   0.012  0.090
3  0.013   0.013  0.065
4  0.007   0.010  0.282


[-1 -1 -1 -1 -1 -1 -1 -1 -1 -1 -1 -1 -1  0 -1 -1 -1 -1 -1 -1  2 -1  0 -1
 -1 -1 -1 -1  0 -1 -1 -1 -1 -1  0  3 -1 -1 -1 -1 -1 -1 -1  0 -1 -1  1  0
 -1 -1 -1  0 -1 -1 -1 -1  0 -1  0  0 -1 -1  0 -1 -1 -1  0  0 -1 -1  0 -1
 -1 -1  0 -1 -1 -1  0  2  0  0  0  0  0 -1 -1 -1  0 -1  0 -1 -1  0 -1  0
 -1  0  0 -1 -1 -1 -1  1  0 -1  0  0 -1 -1 -1  0 -1 -1 -1 -1 -1  0  1 -1
 -1  0  2  0 -1 -1  1 -1 -1 -1  0  0  0 -1 -1  0 -1 -1 -1  0  0 -1 -1 -1
 -1  0 -1 -1 -1  0 -1 -1 -1  0 -1  0  0 -1 -1 -1 -1 -1  0 -1  0  0 -1 -1
 -1 -1 -1  0 -1 -1 -1  1  0  3  1 -1  0  0 -1  0 -1 -1  0  0  2 -1 -1  3
  0  0 -1 -1 -1 -1  0 -1  0  0 -1  0  0  0 -1 -1  0 -1 -1 -1 -1 -1  2  0
 -1 -1 -1 -1 -1 -1 -1 -1 -1 -1 -1 -1 -1 -1  0 -1 -1 -1  0 -1 -1 -1 -1 -1
 -1 -1 -1 -1 -1 -1 -1 -1 -1  0 -1 -1 -1  0  0 -1 -1  0 -1  3  0  2 -1 -1
 -1 -1  0 -1 -1 -1  0 -1  0  0 -1 -1 -1 -1 -1  1 -1

In [28]:
# 클러스터 값으로 그룹화하고 그룹별로 내용 출력 
group_cols = [0,1,3] + columns_list
grouped = df.groupby('Cluster')
for key, group in grouped:
  print('* key :', key)
  print('* number :', len(group))
  print(group.iloc[:, group_cols].head())
  print('\n')

* key : -1
* number : 255
    지역               학교명  유형    과학고  외고_국제고    자사고
0  성북구    서울대학교사범대학부설중학교  국립  0.018   0.007  0.227
1  종로구  서울대학교사범대학부설여자중학교  국립  0.000   0.035  0.043
2  강남구             개원중학교  공립  0.009   0.012  0.090
3  강남구             개포중학교  공립  0.013   0.013  0.065
4  서초구             경원중학교  공립  0.007   0.010  0.282


* key : 0
* number : 102
     지역      학교명  유형  과학고  외고_국제고    자사고
13  서초구  동덕여자중학교  사립  0.0   0.022  0.038
22  강남구    수서중학교  공립  0.0   0.019  0.044
28  서초구    언남중학교  공립  0.0   0.015  0.050
34  강남구    은성중학교  사립  0.0   0.016  0.065
43  송파구    거원중학교  공립  0.0   0.021  0.054


* key : 1
* number : 45
       지역      학교명  유형  과학고  외고_국제고    자사고
46    강동구    동신중학교  사립  0.0     0.0  0.044
103   양천구    신원중학교  공립  0.0     0.0  0.006
118   구로구    개봉중학교  공립  0.0     0.0  0.012
126  영등포구    대림중학교  공립  0.0     0.0  0.050
175   중랑구  혜원여자중학교  사립  0.0     0.0  0.004


* key : 2
* number : 8
      지역    학교명  유형    과학고  외고_국제고    자사고
20   서초구  서초중학교  공립  0.003   0.013  0.085
79

* 데이터 시각화
  - 클러스터 4개 생성

In [33]:
colors= {-1: 'grey', 0: 'coral', 1:'blue', 2:'green', 3:'red', 4:'purple'}

cluster_map = folium.Map(location=[37.55, 126.98], tiles='Stamen Terrain', 
                          zoom_start= 8)

for name, lat, lng, clus in zip(df.학교명, df.위도, df.경도, df.Cluster):
    folium.CircleMarker([lat, lng],
                      radius = 5, 
                      color= colors[clus],
                      file=True, 
                      fill_color =colors[clus],
                      fill_opacity = 0.7,       # 투명도
                      popup=name
  ).add_to(mschool_map)


title_html = '<h3 align="center" style="font-size:20px"><b>서울시 중학교 졸업생의 진학률(</b></h3>'   
mschool_map.get_root().html.add_child(folium.Element(title_html))
mschool_map